In [1]:
import random
import os

import keras
import numpy as np
import shutil
import tensorflow as tf
from keras.callbacks import LambdaCallback
from keras.models import Sequential
from keras.models import Input, Model, load_model
from keras.layers import LSTM, Dropout, Dense
from keras.optimizers import Adam
from keras.callbacks import ModelCheckpoint
from keras.callbacks import EarlyStopping

Using TensorFlow backend.


In [2]:
physical_devices = tf.config.experimental.list_physical_devices('GPU')
assert len(physical_devices) > 0, "Not enough GPU hardware devices available"
tf.config.experimental.set_memory_growth(physical_devices[0], True)

In [3]:
def preprocess_file(file):
    files_content = ''
    with open(file, 'r',encoding='utf-8') as f:
        for line in f:
            x = line.strip() + "]"
            x = x.split(":")[1]
            if len(x) <= 5 :
                continue
            if x[5] == '，':
                files_content += x

    words = sorted(list(files_content))
    counted_words = {}
    for word in words:
        if word in counted_words:
            counted_words[word] += 1
        else:
            counted_words[word] = 1
    #去掉低频的字
    erase = []
    for key in counted_words:
        if counted_words[key] <= 2:
            erase.append(key)
    for key in erase:
        del counted_words[key]
    wordPairs = sorted(counted_words.items(), key=lambda x: -x[1])

    words, _ = zip(*wordPairs)
    words += (" ",)
    # word到id的映射
    word2num = dict((c, i) for i, c in enumerate(words))
    num2word = dict((i, c) for i, c in enumerate(words))
    word2numF = lambda x: word2num.get(x, len(words) - 1)
    return word2numF, num2word, words, files_content


In [14]:
def data_generator():
    i = 0
    while 1:
        y_train = np.zeros(shape=(1, len(words)),dtype='int')
        y_train[0, word2numF(y[i])] = 1

        X_train = np.zeros(shape=(1, 5, len(words)),dtype='int')

        for t, char in enumerate(X[i]):
            X_train[0, t, word2numF(char)] = 1

        yield X_train, y_train
        i += 1

In [15]:
def create_model():
    input = Input(shape = (5,len(words)))
    Lstm  = LSTM(256, return_sequences = True)(input)
    dropout = Dropout(rate=0.5)(Lstm)
    Lstm  = LSTM(128, return_sequences = False)(dropout)
    dropout = Dropout(rate=0.5)(Lstm)
    dense = Dense(len(words), activation='softmax')(dropout)
    
    model = Model(input, dense)  
    model.summary()
    
    return model

In [4]:
file='./poems.txt'
word2numF, num2word, words, files_content = preprocess_file(file)
poems =files_content.split(']') #list形式
poems_num = len(poems) #总数量

In [5]:
word2numF

<function __main__.preprocess_file.<locals>.<lambda>(x)>

In [6]:
words

('，',
 '。',
 ']',
 '不',
 '人',
 '山',
 '无',
 '日',
 '风',
 '云',
 '一',
 '何',
 '有',
 '天',
 '中',
 '来',
 '水',
 '时',
 '月',
 '上',
 '春',
 '生',
 '为',
 '心',
 '相',
 '自',
 '花',
 '此',
 '君',
 '长',
 '秋',
 '如',
 '归',
 '清',
 '白',
 '知',
 '行',
 '年',
 '见',
 '空',
 '去',
 '高',
 '在',
 '江',
 '远',
 '夜',
 '下',
 '未',
 '客',
 '多',
 '寒',
 '里',
 '明',
 '门',
 '子',
 '得',
 '落',
 '青',
 '道',
 '路',
 '出',
 '我',
 '雨',
 '朝',
 '与',
 '思',
 '草',
 '南',
 '事',
 '入',
 '千',
 '处',
 '深',
 '声',
 '金',
 '城',
 '已',
 '树',
 '流',
 '地',
 '三',
 '今',
 '新',
 '色',
 '可',
 '别',
 '万',
 '飞',
 '玉',
 '东',
 '还',
 '家',
 '开',
 '林',
 '独',
 '谁',
 '前',
 '是',
 '复',
 '同',
 '烟',
 '石',
 '游',
 '望',
 '闻',
 '光',
 '将',
 '尽',
 '马',
 '回',
 '酒',
 '欲',
 '西',
 '成',
 '海',
 '方',
 '应',
 '古',
 '雪',
 '重',
 '闲',
 '从',
 '阳',
 '难',
 '书',
 '情',
 '气',
 '身',
 '言',
 '老',
 '鸟',
 '衣',
 '亦',
 '非',
 '更',
 '愁',
 '尘',
 '发',
 '名',
 '向',
 '意',
 '所',
 '然',
 '当',
 '能',
 '_',
 '分',
 '香',
 '歌',
 '旧',
 '看',
 '叶',
 '满',
 '北',
 '平',
 '松',
 '犹',
 '离',
 '幽',
 '起',
 '过',
 '外',
 '故',
 '暮',
 '孤',
 '竹',
 '安'

In [7]:
files_content

'寒随穷律变，春逐鸟声开。初风飘带柳，晚雪间花梅。碧林青旧竹，绿沼翠新苔。芝田初雁去，绮树巧莺来。]晚霞聊自怡，初晴弥可喜。日晃百花色，风动千林翠。池鱼跃不同，园鸟声还异。寄言博通者，知予物外志。]一朝春夏改，隔夜鸟花迁。阴阳深浅叶，晓夕重轻烟。哢莺犹响殿，横丝正网天。珮高兰影接，绶细草纹连。碧鳞惊棹侧，玄燕舞檐前。何必汾阳处，始复有山泉。]夏律昨留灰，秋箭今移晷。峨嵋岫初出，洞庭波渐起。桂白发幽岩，菊黄开灞涘。运流方可叹，含毫属微理。]寒惊蓟门叶，秋发小山枝。松阴背日转，竹影避风移。提壶菊花岸，高兴芙蓉池。欲知凉气早，巢空燕不窥。]爽气浮丹阙，秋光澹紫宫。衣碎荷疏影，花明菊点丛。袍轻低草露，盖侧舞松风。散岫飘云叶，迷路飞烟鸿。砌冷兰凋佩，闺寒树陨桐。别鹤栖琴里，离猿啼峡中。落野飞星箭，弦虚半月弓。芳菲夕雾起，暮色满房栊。]山亭秋色满，岩牖凉风度。疏兰尚染烟，残菊犹承露。古石衣新苔，新巢封古树。历览情无极，咫尺轮光暮。]秦川雄帝宅，函谷壮皇居。绮殿千寻起，离宫百雉余。连薨遥接汉，飞观迥凌虚。云日隐层阙，风烟出绮疏。岩廊罢机务，崇文聊驻辇。玉匣启龙图，金绳披凤篆。韦编断仍续，缥帙舒还卷。对此乃淹留，欹案观坟典。移步出词林，停舆欣武宴。雕弓写明月，骏马疑流电。惊雁落虚弦，啼猿悲急箭。阅赏诚多美，于兹乃忘倦。鸣笳临乐馆，眺听欢芳节。急管韵朱弦，清歌凝白雪。彩凤肃来仪，玄鹤纷成列。去兹郑卫声，雅音方可悦。芳辰追逸趣，禁苑信多奇。桥形通汉上，峰势接云危。烟霞交隐映，花鸟自参差。何如肆辙迹，万里赏瑶池。飞盖去芳园，兰桡游翠渚。萍间日彩乱，荷处香风举。桂楫满中川，弦歌振长屿。岂必汾河曲，方为欢宴所。落日双阙昏，回舆九重暮。长烟散初碧，皎月澄轻素。搴幌玩琴书，开轩引云雾。斜汉耿层阁，清风摇玉树。欢乐难再逢，芳辰良可惜。玉酒泛云罍，兰殽陈绮席。千钟合尧禹，百兽谐金石。得志重寸阴，忘怀轻尺璧。建章欢赏夕，二八尽妖妍。罗绮昭阳殿，芬芳玳瑁筵。佩移星正动，扇掩月初圆。无劳上悬圃，即此对神仙。以兹游观极，悠然独长想。披卷览前踪，抚躬寻既往。望古茅茨约，瞻今兰殿广。人道恶高危，虚心戒盈荡。奉天竭诚敬，临民思惠养。纳善察忠谏，明科慎刑赏。六五诚难继，四三非易仰。广待淳化敷，方嗣云亭响。]塞外悲风切，交河冰已结。瀚海百重波，阴山千里雪。迥戍危烽火，层峦引高节。悠悠卷旆旌，饮马出长城。寒沙连骑迹，朔

In [8]:
poems = [myL.replace('，', '') for myL in poems]
poems = [myL.replace('。', '') for myL in poems]

In [9]:
poems

['寒随穷律变春逐鸟声开初风飘带柳晚雪间花梅碧林青旧竹绿沼翠新苔芝田初雁去绮树巧莺来',
 '晚霞聊自怡初晴弥可喜日晃百花色风动千林翠池鱼跃不同园鸟声还异寄言博通者知予物外志',
 '一朝春夏改隔夜鸟花迁阴阳深浅叶晓夕重轻烟哢莺犹响殿横丝正网天珮高兰影接绶细草纹连碧鳞惊棹侧玄燕舞檐前何必汾阳处始复有山泉',
 '夏律昨留灰秋箭今移晷峨嵋岫初出洞庭波渐起桂白发幽岩菊黄开灞涘运流方可叹含毫属微理',
 '寒惊蓟门叶秋发小山枝松阴背日转竹影避风移提壶菊花岸高兴芙蓉池欲知凉气早巢空燕不窥',
 '爽气浮丹阙秋光澹紫宫衣碎荷疏影花明菊点丛袍轻低草露盖侧舞松风散岫飘云叶迷路飞烟鸿砌冷兰凋佩闺寒树陨桐别鹤栖琴里离猿啼峡中落野飞星箭弦虚半月弓芳菲夕雾起暮色满房栊',
 '山亭秋色满岩牖凉风度疏兰尚染烟残菊犹承露古石衣新苔新巢封古树历览情无极咫尺轮光暮',
 '秦川雄帝宅函谷壮皇居绮殿千寻起离宫百雉余连薨遥接汉飞观迥凌虚云日隐层阙风烟出绮疏岩廊罢机务崇文聊驻辇玉匣启龙图金绳披凤篆韦编断仍续缥帙舒还卷对此乃淹留欹案观坟典移步出词林停舆欣武宴雕弓写明月骏马疑流电惊雁落虚弦啼猿悲急箭阅赏诚多美于兹乃忘倦鸣笳临乐馆眺听欢芳节急管韵朱弦清歌凝白雪彩凤肃来仪玄鹤纷成列去兹郑卫声雅音方可悦芳辰追逸趣禁苑信多奇桥形通汉上峰势接云危烟霞交隐映花鸟自参差何如肆辙迹万里赏瑶池飞盖去芳园兰桡游翠渚萍间日彩乱荷处香风举桂楫满中川弦歌振长屿岂必汾河曲方为欢宴所落日双阙昏回舆九重暮长烟散初碧皎月澄轻素搴幌玩琴书开轩引云雾斜汉耿层阁清风摇玉树欢乐难再逢芳辰良可惜玉酒泛云罍兰殽陈绮席千钟合尧禹百兽谐金石得志重寸阴忘怀轻尺璧建章欢赏夕二八尽妖妍罗绮昭阳殿芬芳玳瑁筵佩移星正动扇掩月初圆无劳上悬圃即此对神仙以兹游观极悠然独长想披卷览前踪抚躬寻既往望古茅茨约瞻今兰殿广人道恶高危虚心戒盈荡奉天竭诚敬临民思惠养纳善察忠谏明科慎刑赏六五诚难继四三非易仰广待淳化敷方嗣云亭响',
 '塞外悲风切交河冰已结瀚海百重波阴山千里雪迥戍危烽火层峦引高节悠悠卷旆旌饮马出长城寒沙连骑迹朔吹断边声胡尘清玉塞羌笛韵金钲绝漠干戈戢车徒振原隰都尉反龙堆将军旋马邑扬麾氛雾静纪石功名立荒裔一戎衣灵台凯歌入',
 '执契静三边持衡临万姓玉彩辉关烛金华流日镜无为宇宙清有美璇玑正皎佩星连景飘衣云结庆戢武耀七德升文辉九功烟波澄旧碧尘火息前红霜野韬莲剑关城罢月弓钱缀榆

In [11]:
X = []
y = []
for i in range(len(poems)):
    for j in range(len(poems[i])-6):
        X.append(poems[i][j:j+5])
        y.append(poems[i][j+6])

In [13]:
X[0]

'寒随穷律变'

In [12]:
len(y)

1373134

In [16]:
batch_size = 2048  # 批大小
opt = Adam(lr=0.0001, decay=1e-6)  # 使用Adam优化器

model = create_model()

# 编译模型
model.compile(loss='categorical_crossentropy',
              optimizer=opt,
              metrics=['accuracy'])

Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         (None, 5, 5552)           0         
_________________________________________________________________
lstm_1 (LSTM)                (None, 5, 256)            5948416   
_________________________________________________________________
dropout_1 (Dropout)          (None, 5, 256)            0         
_________________________________________________________________
lstm_2 (LSTM)                (None, 128)               197120    
_________________________________________________________________
dropout_2 (Dropout)          (None, 128)               0         
_________________________________________________________________
dense_1 (Dense)              (None, 5552)              716208    
Total params: 6,861,744
Trainable params: 6,861,744
Non-trainable params: 0
_________________________________________________

In [17]:
model_dir = os.path.join("./BestTextModel")
output_model_file = os.path.join(model_dir,
                                 "Model.h5")

callbacks = [
    ModelCheckpoint(output_model_file, save_best_only = False),
]

In [12]:
#model.load_weights("./BestTextModel/BestModel.h5")

In [13]:
history = model.fit_generator(
  generator=data_generator(),
  steps_per_epoch=batch_size,
  verbose=2,
  epochs=6000,
  callbacks=callbacks
)

Epoch 1/6000
 - 7s - loss: 6.8143 - accuracy: 0.0156
Epoch 2/6000
 - 5s - loss: 6.8242 - accuracy: 0.0039
Epoch 3/6000
 - 5s - loss: 6.9799 - accuracy: 0.0078
Epoch 4/6000
 - 5s - loss: 7.0861 - accuracy: 0.0078
Epoch 5/6000
 - 5s - loss: 6.9768 - accuracy: 0.0039
Epoch 6/6000
 - 6s - loss: 7.0335 - accuracy: 0.0000e+00
Epoch 7/6000
 - 6s - loss: 7.0125 - accuracy: 0.0000e+00
Epoch 8/6000
 - 4s - loss: 7.2108 - accuracy: 0.0078
Epoch 9/6000
 - 6s - loss: 7.1259 - accuracy: 0.0039
Epoch 10/6000
 - 5s - loss: 6.9904 - accuracy: 0.0078
Epoch 11/6000
 - 5s - loss: 7.2535 - accuracy: 0.0000e+00
Epoch 12/6000
 - 5s - loss: 7.0847 - accuracy: 0.0078
Epoch 13/6000
 - 5s - loss: 6.9113 - accuracy: 0.0000e+00
Epoch 14/6000
 - 6s - loss: 6.8020 - accuracy: 0.0039
Epoch 15/6000
 - 6s - loss: 6.6390 - accuracy: 0.0234
Epoch 16/6000
 - 5s - loss: 6.5510 - accuracy: 0.0156
Epoch 17/6000
 - 7s - loss: 6.9358 - accuracy: 0.0156
Epoch 18/6000
 - 7s - loss: 6.8800 - accuracy: 0.0039
Epoch 19/6000
 - 5s -

Epoch 151/6000
 - 6s - loss: 7.1580 - accuracy: 0.0039
Epoch 152/6000
 - 4s - loss: 7.2395 - accuracy: 0.0117
Epoch 153/6000
 - 5s - loss: 7.1338 - accuracy: 0.0352
Epoch 154/6000
 - 5s - loss: 7.3476 - accuracy: 0.0117
Epoch 155/6000
 - 6s - loss: 7.4856 - accuracy: 0.0078
Epoch 156/6000
 - 6s - loss: 7.4567 - accuracy: 0.0117
Epoch 157/6000
 - 7s - loss: 7.3163 - accuracy: 0.0117
Epoch 158/6000
 - 6s - loss: 7.4102 - accuracy: 0.0156
Epoch 159/6000
 - 6s - loss: 7.6610 - accuracy: 0.0156
Epoch 160/6000
 - 6s - loss: 7.5241 - accuracy: 0.0195
Epoch 161/6000
 - 6s - loss: 7.0524 - accuracy: 0.0156
Epoch 162/6000
 - 5s - loss: 6.7958 - accuracy: 0.0156
Epoch 163/6000
 - 6s - loss: 6.8409 - accuracy: 0.0078
Epoch 164/6000
 - 6s - loss: 6.7275 - accuracy: 0.0000e+00
Epoch 165/6000
 - 6s - loss: 6.8901 - accuracy: 0.0039
Epoch 166/6000
 - 5s - loss: 6.7979 - accuracy: 0.0078
Epoch 167/6000
 - 6s - loss: 6.9619 - accuracy: 0.0195
Epoch 168/6000
 - 5s - loss: 7.2871 - accuracy: 0.0117
Epoch 

Epoch 299/6000
 - 6s - loss: 7.6169 - accuracy: 0.0117
Epoch 300/6000
 - 5s - loss: 7.6000 - accuracy: 0.0078
Epoch 301/6000
 - 5s - loss: 7.5088 - accuracy: 0.0117
Epoch 302/6000
 - 5s - loss: 7.3696 - accuracy: 0.0078
Epoch 303/6000
 - 5s - loss: 7.4511 - accuracy: 0.0156
Epoch 304/6000
 - 5s - loss: 7.2843 - accuracy: 0.0078
Epoch 305/6000
 - 6s - loss: 7.4716 - accuracy: 0.0078
Epoch 306/6000
 - 6s - loss: 7.4019 - accuracy: 0.0039
Epoch 307/6000
 - 5s - loss: 7.0427 - accuracy: 0.0156
Epoch 308/6000
 - 7s - loss: 7.0725 - accuracy: 0.0078
Epoch 309/6000
 - 6s - loss: 7.2661 - accuracy: 0.0078
Epoch 310/6000
 - 6s - loss: 7.3375 - accuracy: 0.0156
Epoch 311/6000
 - 7s - loss: 6.9859 - accuracy: 0.0039
Epoch 312/6000
 - 6s - loss: 7.0119 - accuracy: 0.0117
Epoch 313/6000
 - 6s - loss: 6.8796 - accuracy: 0.0078
Epoch 314/6000
 - 6s - loss: 6.6547 - accuracy: 0.0117
Epoch 315/6000
 - 5s - loss: 6.8570 - accuracy: 0.0156
Epoch 316/6000
 - 5s - loss: 7.1384 - accuracy: 0.0117
Epoch 317/

 - 7s - loss: 8.0738 - accuracy: 0.0039
Epoch 447/6000
 - 6s - loss: 7.8857 - accuracy: 0.0039
Epoch 448/6000
 - 5s - loss: 7.2924 - accuracy: 0.0117
Epoch 449/6000
 - 5s - loss: 7.6520 - accuracy: 0.0000e+00
Epoch 450/6000
 - 5s - loss: 7.5648 - accuracy: 0.0156
Epoch 451/6000
 - 6s - loss: 7.9094 - accuracy: 0.0078
Epoch 452/6000
 - 7s - loss: 7.2386 - accuracy: 0.0156
Epoch 453/6000
 - 5s - loss: 7.7661 - accuracy: 0.0039
Epoch 454/6000
 - 6s - loss: 7.6151 - accuracy: 0.0000e+00
Epoch 455/6000
 - 5s - loss: 7.8805 - accuracy: 0.0078
Epoch 456/6000
 - 5s - loss: 7.8110 - accuracy: 0.0039
Epoch 457/6000
 - 7s - loss: 7.4707 - accuracy: 0.0000e+00
Epoch 458/6000
 - 6s - loss: 7.7050 - accuracy: 0.0078
Epoch 459/6000
 - 6s - loss: 7.5860 - accuracy: 0.0000e+00
Epoch 460/6000
 - 6s - loss: 6.9244 - accuracy: 0.0156
Epoch 461/6000
 - 6s - loss: 7.0300 - accuracy: 0.0078
Epoch 462/6000
 - 5s - loss: 7.1765 - accuracy: 0.0078
Epoch 463/6000
 - 6s - loss: 7.5055 - accuracy: 0.0000e+00
Epoch

Epoch 594/6000
 - 5s - loss: 7.6760 - accuracy: 0.0000e+00
Epoch 595/6000
 - 5s - loss: 7.5085 - accuracy: 0.0117
Epoch 596/6000
 - 5s - loss: 7.6953 - accuracy: 0.0078
Epoch 597/6000
 - 4s - loss: 7.8400 - accuracy: 0.0039
Epoch 598/6000
 - 6s - loss: 7.9116 - accuracy: 0.0078
Epoch 599/6000
 - 5s - loss: 7.8896 - accuracy: 0.0117
Epoch 600/6000
 - 5s - loss: 8.0210 - accuracy: 0.0078
Epoch 601/6000
 - 7s - loss: 7.8817 - accuracy: 0.0039
Epoch 602/6000
 - 6s - loss: 7.8501 - accuracy: 0.0039
Epoch 603/6000
 - 4s - loss: 7.9431 - accuracy: 0.0039
Epoch 604/6000
 - 6s - loss: 7.2870 - accuracy: 0.0117
Epoch 605/6000
 - 6s - loss: 7.8510 - accuracy: 0.0078
Epoch 606/6000
 - 5s - loss: 7.8958 - accuracy: 0.0117
Epoch 607/6000
 - 5s - loss: 7.7279 - accuracy: 0.0078
Epoch 608/6000
 - 5s - loss: 7.5412 - accuracy: 0.0117
Epoch 609/6000
 - 6s - loss: 7.6429 - accuracy: 0.0039
Epoch 610/6000
 - 6s - loss: 7.3810 - accuracy: 0.0039
Epoch 611/6000
 - 5s - loss: 7.3038 - accuracy: 0.0234
Epoch 

...

Epoch 4844/6000
 - 5s - loss: 7.4795 - accuracy: 0.0430
Epoch 4845/6000
 - 4s - loss: 7.7605 - accuracy: 0.0273
Epoch 4846/6000
 - 5s - loss: 8.0458 - accuracy: 0.0312
Epoch 4847/6000
 - 5s - loss: 8.1435 - accuracy: 0.0234
Epoch 4848/6000
 - 4s - loss: 7.7146 - accuracy: 0.0273
Epoch 4849/6000
 - 4s - loss: 7.6567 - accuracy: 0.0469
Epoch 4850/6000
 - 4s - loss: 7.7537 - accuracy: 0.0273
Epoch 4851/6000
 - 5s - loss: 8.9647 - accuracy: 0.0117
Epoch 4852/6000
 - 4s - loss: 7.9226 - accuracy: 0.0195
Epoch 4853/6000
 - 5s - loss: 7.3973 - accuracy: 0.0312
Epoch 4854/6000
 - 5s - loss: 7.5765 - accuracy: 0.0195
Epoch 4855/6000
 - 5s - loss: 7.9659 - accuracy: 0.0430
Epoch 4856/6000
 - 5s - loss: 8.2026 - accuracy: 0.0234
Epoch 4857/6000
 - 4s - loss: 7.5857 - accuracy: 0.0195
Epoch 4858/6000
 - 4s - loss: 8.0232 - accuracy: 0.0469
Epoch 4859/6000
 - 4s - loss: 8.0043 - accuracy: 0.0312
Epoch 4860/6000
 - 4s - loss: 9.1502 - accuracy: 0.0078
Epoch 4861/6000
 - 4s - loss: 8.3584 - accuracy:

 - 6s - loss: 11.1785 - accuracy: 0.0000e+00
Epoch 4991/6000
 - 5s - loss: 11.1273 - accuracy: 0.0000e+00
Epoch 4992/6000
 - 4s - loss: 11.2332 - accuracy: 0.0078
Epoch 4993/6000
 - 5s - loss: 10.4273 - accuracy: 0.0273
Epoch 4994/6000
 - 4s - loss: 9.8695 - accuracy: 0.0312
Epoch 4995/6000
 - 4s - loss: 9.6070 - accuracy: 0.0391
Epoch 4996/6000
 - 4s - loss: 9.9639 - accuracy: 0.0312
Epoch 4997/6000
 - 5s - loss: 9.6875 - accuracy: 0.0312
Epoch 4998/6000
 - 4s - loss: 9.8412 - accuracy: 0.0625
Epoch 4999/6000
 - 5s - loss: 8.9428 - accuracy: 0.0938
Epoch 5000/6000
 - 5s - loss: 9.3909 - accuracy: 0.0820
Epoch 5001/6000
 - 5s - loss: 10.5677 - accuracy: 0.0586
Epoch 5002/6000
 - 4s - loss: 10.7162 - accuracy: 0.0625
Epoch 5003/6000
 - 5s - loss: 9.6453 - accuracy: 0.1055
Epoch 5004/6000
 - 4s - loss: 9.2773 - accuracy: 0.0781
Epoch 5005/6000
 - 4s - loss: 8.9672 - accuracy: 0.0820
Epoch 5006/6000
 - 4s - loss: 8.5509 - accuracy: 0.0820
Epoch 5007/6000
 - 4s - loss: 9.2227 - accuracy: 0

Epoch 5137/6000
 - 4s - loss: 7.5511 - accuracy: 0.0273
Epoch 5138/6000
 - 4s - loss: 7.9233 - accuracy: 0.0312
Epoch 5139/6000
 - 5s - loss: 7.2507 - accuracy: 0.0469
Epoch 5140/6000
 - 4s - loss: 7.7504 - accuracy: 0.0469
Epoch 5141/6000
 - 4s - loss: 7.9795 - accuracy: 0.0469
Epoch 5142/6000
 - 5s - loss: 7.5098 - accuracy: 0.0625
Epoch 5143/6000
 - 5s - loss: 8.5141 - accuracy: 0.0391
Epoch 5144/6000
 - 4s - loss: 7.2860 - accuracy: 0.0391
Epoch 5145/6000
 - 4s - loss: 7.3496 - accuracy: 0.0039
Epoch 5146/6000
 - 5s - loss: 7.0382 - accuracy: 0.0391
Epoch 5147/6000
 - 5s - loss: 7.1870 - accuracy: 0.0117
Epoch 5148/6000
 - 4s - loss: 7.3552 - accuracy: 0.0430
Epoch 5149/6000
 - 4s - loss: 8.4321 - accuracy: 0.0156
Epoch 5150/6000
 - 5s - loss: 8.6132 - accuracy: 0.0156
Epoch 5151/6000
 - 4s - loss: 7.4546 - accuracy: 0.0273
Epoch 5152/6000
 - 5s - loss: 7.6782 - accuracy: 0.0312
Epoch 5153/6000
 - 5s - loss: 7.4723 - accuracy: 0.0273
Epoch 5154/6000
 - 4s - loss: 7.3522 - accuracy:

Epoch 5284/6000
 - 4s - loss: 8.1407 - accuracy: 0.0156
Epoch 5285/6000
 - 4s - loss: 8.2716 - accuracy: 0.0156
Epoch 5286/6000
 - 5s - loss: 7.6233 - accuracy: 0.0234
Epoch 5287/6000
 - 4s - loss: 8.6358 - accuracy: 0.0039
Epoch 5288/6000
 - 4s - loss: 7.7805 - accuracy: 0.0195
Epoch 5289/6000
 - 4s - loss: 7.6373 - accuracy: 0.0156
Epoch 5290/6000
 - 4s - loss: 7.7033 - accuracy: 0.0117
Epoch 5291/6000
 - 5s - loss: 7.6101 - accuracy: 0.0156
Epoch 5292/6000
 - 5s - loss: 7.7569 - accuracy: 0.0234
Epoch 5293/6000
 - 4s - loss: 7.3155 - accuracy: 0.0273
Epoch 5294/6000
 - 4s - loss: 7.2127 - accuracy: 0.0078
Epoch 5295/6000
 - 4s - loss: 7.9538 - accuracy: 0.0312
Epoch 5296/6000
 - 4s - loss: 7.8769 - accuracy: 0.0352
Epoch 5297/6000
 - 4s - loss: 7.8073 - accuracy: 0.0352
Epoch 5298/6000


KeyboardInterrupt: 